In [1]:
from termcolor import colored
import jsonlines

In [ ]:
conf_1 = {
    "unique_captures": {"param_name": "--unique_captures", "value": "", 
        "description": "if true, each entity appears only once in the entire dataset."
    },
    "distractor": {"param_name": "--distractor", "value": "PERSON", 
        "description": " a known entity type, which is NOT of the target entity type."
    },
    "suffix": {"param_name": "--suffix", "value": "_schools", 
        "description": "suffix for the output files"
    },
    "version_name": {"param_name": "--version_name", "value": "py_scripts", 
        "description": ""
    },
    "wandb_project": {"param_name": "--wandb_project", "value": "review", 
        "description": ""
    },
    "experiment_suffix": {"param_name": "--experiment_suffix", "value": "with_superclass", 
        "description": ""
    },
    "superclass_tag": {"param_name": "--superclass_tag", "value": "ORG", 
        "description": "If left empty,"
    },
    "target_tag": {"param_name": "--target_tag", "value": " SCHOOL", 
        "description": ""
    },
    "patterns_file": {
        "param_name": "--patterns_file", 
        "value": " ../src/school_patterns.json", 
        "description": ""
    },
    "dataset_name": {
        "param_name": "--dataset_name", 
        "value": " schools", 
        "description": ""
    },
    "hearst_patterns": {
        "param_name": "--hearst_patterns", 
        "value": " ../src/school_hearst.json", 
         "description": ""
    },
    "hearst_limit": {
        "param_name": "--hearst_limit", 
        "value": " 10000", 
        "description": ""
    },
    "dataset_path": {"param_name": '--dataset_path", "value": " ../data/schools', 
                        "description": ""}
}

In [2]:
unique_captures = "--unique_captures" # if true, each entity appears only once in the entire dataset.
distractor = "--distractor PERSON" # a known entity type, which is NOT of the target entity type.
prefix = "--prefix schools_" # suffix for the output files
version_name = "--version_name school"
wandb_project = "--wandb_project schools"
experiment_suffix = "--experiment_suffix only-hearst"
superclass_tag = "--superclass_tag ORG"
target_tag = "--target_tag SCHOOL"
patterns_file = "--patterns_file school_patterns.json"
dataset_name = "--dataset_name schools"
hearst_patterns = "--hearst_patterns school_hearst.json"
hearst_limit = "--hearst_limit 30000"
dataset_path= f'--dataset_path data/schools'
use_only_hearst = "--use_only_hearst"

In [6]:
!wc -l data/lists/*

     35 data/lists/certificate.txt
   2746 data/lists/comedians.txt
   2811 data/lists/comedians_dirty.txt
  11309 data/lists/exemplars.txt
     38 data/lists/genres.txt
  16177 data/lists/hearst_musicians.txt
  16170 data/lists/hearst_musicians_bigger.txt
      5 data/lists/institute.txt
    270 data/lists/instruments.txt
  87953 data/lists/musicians_from_wikipedia.txt
     35 data/lists/old_certificate.txt
      5 data/lists/old_institute.txt
     11 data/lists/pieces.txt
     64 data/lists/random_people.txt
     28 data/lists/roles.txt
    199 data/lists/sample_musicians.txt
 137856 total


In [ ]:
!mkdir -p data/spike_matches/hearst/

In [7]:
!python src/collect_data.py {unique_captures} {distractor} {prefix} {superclass_tag} {patterns_file} {hearst_patterns}

100%|█████████████████████████████████████████████| 4/4 [01:18<00:00, 19.74s/it]
{'0': {'query': '$[l={institute}]institutes $such as <E>positive:[e=ORG]Yale', 'type': 'syntactic', 'case_strategy': 'ignore', 'label': 'positive', 'lists': ['institute'], 'limit': 100}, '1': {'query': '<E>positive:[e=ORG]Yale is an $[l={institute}]institute', 'type': 'syntactic', 'case_strategy': 'ignore', 'label': 'positive', 'lists': ['institute'], 'limit': 100}, '2': {'query': '$[l={institute}]institutes $including <E>positive:[e=ORG]Yale', 'type': 'syntactic', 'case_strategy': 'ignore', 'label': 'positive', 'lists': ['institute'], 'limit': 100}, '3': {'query': 'Jane got her $[w={certificate}]degree from <E>positive:[e=ORG]Yale', 'type': 'syntactic', 'case_strategy': 'ignore', 'label': 'positive', 'lists': ['institute', 'certificate'], 'limit': 100}, '4': {'query': 'Jane $graduated from <E>positive:[e=ORG]Yale', 'type': 'syntactic', 'case_strategy': 'ignore', 'label': 'positive', 'lists': ['institute',

In [8]:
!wc -l data/spike_matches/positive/schools_*

     89 data/spike_matches/positive/schools_0.jsonl
     84 data/spike_matches/positive/schools_1.jsonl
     89 data/spike_matches/positive/schools_2.jsonl
     83 data/spike_matches/positive/schools_3.jsonl
     87 data/spike_matches/positive/schools_4.jsonl
   3089 data/spike_matches/positive/schools_hearst.jsonl
   3521 total


In [27]:
!head -5 data/lists/exemplars.txt

North Georgia Technical College
The Tam O'Shanter Golf
Ngata Memorial College
Boyce Bible School
Hue University of Medicine and Pharmacy


In [ ]:
# make sure the spike matches make sense
! head -5 data/spike_matches/positive/0_schools.jsonl

In [9]:
!python src/tag_dataset.py {prefix} {version_name} {superclass_tag} {target_tag} {dataset_name} {use_only_hearst}

./data/spike_matches/positive/schools_4.jsonl
./data/spike_matches/positive/schools_0.jsonl
./data/spike_matches/positive/schools_1.jsonl
./data/spike_matches/positive/schools_2.jsonl
./data/spike_matches/positive/schools_3.jsonl
Number of negatives:  11026
Number of positives:  2728
invalids:  2137
same_sent:  0


In [12]:
# make sure the tagged data makes sense
with jsonlines.open("./data/schools/dataset_school.jsonl", 'r') as f:
    for i, line in enumerate(f):
        color_text = [x[0] if x[1] == "O" else colored(x[0], 'red') if "ORG" in x[1] else colored(x[0], 'green') for x in line["sent_items"]]
        print(i, line["id"], " ".join(color_text))
        print()

0 89220 On the U.S. Federal Budget , Meeks supports Social Security and Medicare and wants to balance the budget , lower the national debt while sending money to education , environment and national defense .

1 64742 Kim Cascone ( December 21 , 1955 ) is an American composer of electronic music who is known for his releases in the ambient , drone , industrial and electro - acoustic genre on his own record label , Silent Records .

2 9120 The Wright - Brooks House , also known as the Daniel Pratt House , is a single - family home located at 122 North High Street in Marshall , Michigan .

3 53830 He was most inspired by the illustrations he had seen in " Scribner 's Magazine " and " The Saturday Evening Post " by Norman Rockwell and Frederic Remington .

4 71103 The railway line between and Walton was proposed by the Liverpool , Ormskirk and Preston Railway ( LO&PJ ) and authorised in 1846 ; later that year the LO&PJ was amalgamated with the East Lancashire Railway ( ELR ) , which opene

621 10565 He was also a very accomplished ice speedway rider and member of the Soviet team that finished third in the World Team Cup final in 1973 .

622 35670 Hagar International was named after the biblical character Hagar from Genesis 16 - 21 .

623 584404 He began high school at Christ the King Regional High School in Middle Village , Queens before transferring to Brooklyn College Academy before his sophomore year and helped lead the team to the Public Schools Athletic League title in his first season with the Bobcats .

624 66826 After six days of marching through Jago 's desert - like terrain and enduring dust - storms , the Ghosts reach their objective : Hinzerhaus , dubbed the " house at the end of the world " .

625 42547 UFC 6 featured the crowning of the first UFC Champion to win the title in a non - tournament format .

626 72686 Perhaps the latest chapbook example is " The Adventures of Sir Richard Whittingon " , printed by J. Cheney , 1788–1808 which is quoted in full by 

1236 51978 Dr. Sly has served on the Scientific Review Board and Medical Advisory Board for the Howard Hughes Medical Institute , the Board of Scientific Overseers for the Jackson Laboratory , and on many scientific societies and other foundations .

1237 19366 Ankara Atatürk Lisesi ( " Ankara Atatürk High School " ) , is an Anatolian High School located near Sıhhiye district of Çankaya , Ankara .

1238 59572 Veblen expanded upon Adam Smith ’s assessment of the rich , stating that “ The leisure class used charitable activities as one of the ultimate benchmarks of the highest standard of living ” ( Ganley , 1998 ) .

1239 11904 He played in Major League Baseball ( MLB ) from 1996 through 2010 for the Pittsburgh Pirates , Oakland Athletics , Chicago Cubs , Milwaukee Brewers , and Kansas City Royals .

1240 57828 The Message Board 's online connectivity is now defunct , along with the shutdown of its foundational WiiConnect24 service .

1241 20315 Cadets are also allowed to attend special

1888 47882 He averaged 10 points per game for Windsor including a 16 - point performance vs KW Waterloo Kitchener .

1889 459779 In 1968 , the [ [ Pakistan Naval War College|Naval War College ] ] was established in [ [ Lahore ] ] , whose curriculum is very similar to the [ [ Naval War College ] ] in the [ [ United States ] ] , is a primary military staff college which offers critical thinking techniques and developing ideas for naval warfare to the officers in the army and the air force .

1890 97014 On June 24 , 2016 , he joined ASVEL Basket of the LNB Pro A and of the Champions League .

1891 195163 ( Dr. Hart was subsequently named the president of Temple University and is currently the president of the University of Arizona . )

1892 397858 She was on the advisory council for the School of Art at Goldsmiths ' College .

1893 553112 It is an unaided English medium School and prepares students for the ten year Secondary School Leaving certificate ( S.S.L.C ) examination of the Kerala

2543 578109 The University of Northern British Columbia and Siiwiixo'osxwim Wilnataahl Gitksan Society ( Gitksan Language Society ) set up a Developmental Standard Term Certificate program offered through Northwest Community College , with all courses offered in Hazelton , BC .

2544 63032 The Lady Techsters , currently led by head coach Brooke Stoehr , has been the most successful Louisiana Tech athletic team .

2545 6048 Milošević received U.S. envoy Richard Holbrook at the palace before the NATO bombing of Yugoslavia began ; Milošević later officially resigned his presidency in front of the palace fireplace .

2546 37665 Donnelly appeared in 190 Major League Baseball ( MLB ) games between 1944 and 1951 for the St. Louis Cardinals , Philadelphia Phillies , and Boston Braves .

2547 77701 The NSU Prinz ( Prince ) is an automobile which was produced in West Germany by the NSU Motorenwerke AG from 1958 to 1973 .

2548 59509 It was during this time that he wrote " The Engineers and the P

...

10853 51563 Real estate developers E.A. McCallum , E. M. McCallum and Walter H.A. Hill began construction of the McCallum - Hill office building in 1912 .

10854 47642 Other businesses under separate management but located on Thanksgiving Point 's campuses include Brick Canvas Studios , Holdman Studios and Glass Art Institute , Larry H. Miller Megaplex Theatres , and Thanksgiving Point Golf Course .

10855 502440 His two most influential surveys were in the 20th century ; the first in 1912 to determine Maryland 's border with West Virginia , and the second in 1927 on the Red River to determine the border between Texas and Oklahoma .

10856 67373 Extending UNIFIL 's mandate for another year , the Council commended the force in establishing a new strategic environment in southern Lebanon and its co - operation with the Lebanese Armed Forces .

10857 6089 The Hitlerjugend Waffen SS were notoriously brutal and murdered several Canadian Prisoners of War in the early stages of the Normandy C

11524 289946 He moved back to North Carolina in the 1970s and went on to become a teacher , serving as the English department chair at Campbell College from 1974 to 1978 before becoming a professor of English at the University of North Carolina at Pembroke and the editor of " Pembroke Magazine " from 1978 until retiring in 2010 .

11525 52406 Additionally , it is involved in the diagnosis and management of dry mouth conditions ( such as Sjögren 's syndrome ) and non - dental chronic orofacial pain , such as burning mouth syndrome , trigeminal neuralgia and temporomandibular joint disorder .

11526 204389 She finished her PhD studies in 1987 at the Faculty of Economics in Subotica , which belongs to the University of Novi Sad .

11527 89440 He won the Dick Howser Trophy and the National Pitcher of the Year Award .

11528 49404 Since 1970 , Feyl has lived in Berlin working as a freelance writer .

11529 84221 A list of events was compiled by the National Quality Forum and updated in 2012

12181 89215 Meeks was a member of the New York State Assembly ( 31st D. ) from 1993 to 1998 , sitting in the 190th , 191st , and 192nd New York State Legislatures .

12182 99042 He previously served in various command positions within the Jefferson Parish Sheriff ’s Office before being elected in 2007 after the death of then Sheriff Harry Lee .

12183 568398 Day entered medical school at age 18 at the University of Manchester , where he graduated in 1970 .

12184 56379 Giri completed his Intermediate in Science degree from the Central Campus of Technology , Dharan and Bachelor in Science from Mahendra Morang Adarsha Bahumukhi Campus in Biratnagar .

12185 101644 Mililani B. Trask , her younger sister , is an attorney on the Big Island and was a trustee of the Office of Hawaiian Affairs created by the 1978 Hawaii State Constitutional Convention to administer lands held in trust for Native Hawaiians and use the revenue to fund Native Hawaiian programs .

12186 24294 After a weak start , 

12811 61522 The medical college is affiliated with one private sector teaching hospital running by SSMC Sughra Shafi Medical Complex for undergraduate and post graduate medical education & training .

12812 60737 In the report , Ismayilova quoted Vasif Movsumov , executive director of the Baku - based Anti - Corruption Foundation , as saying the ownership of the said companies by Parliament Members is a violation of law .

12813 100490 In 1929 , the Texas legislature designated the Zivley version of the Old San Antonio Road as one of the historic trails of Texas .

12814 423180 Despite Weil 's and the women 's clubs hard work in North Carolina in support of the Nineteenth Amendment , the North Carolina state legislature refused to ratify the amendment , instead , the state of Tennessee cast the final vote to gain women the right to vote in the United States .

12815 542033 He eventually earned a scholarship in 2004 to Bacone College in Muskogee Oklahoma where he became the Red River At

13416 96857 All language instances of Wikipedia have since been moved over to MediaWiki .

13417 23498 It is used by San Diego High School for local high school sporting and other events .

13418 94583 Miura has cited Kenji Maruyama and Hideo Nakai as favorite authors .

13419 43937 Among the Little Ivies are the " Little Three " , a term used by Amherst College , Wesleyan University and Williams College , and " Maine Big Three " , a term used by Colby College , Bates College and Bowdoin College .

13420 55438 She is a member of the Triple Gold Club ( not officially recognized by the IIHF for women ) as one of only three women to win the Clarkson Cup , an Olympic gold medal and an IIHF Women 's World Championship gold medal .

13421 42087 She was a Vancouver British Columbia Dancesport Champion four times , from 1998 to 2002 .

13422 2205 Afterwards , a waiting list of students is posted online on the Brown College website .

13423 190512 She studied Jurisprudence at the university the

In [ ]:
!wc -l data/schools/*

In [16]:
!python src/train.py {wandb_project} {experiment_suffix} {version_name}  {superclass_tag} {target_tag} {dataset_path} --epochs 3

Some weights of the model checkpoint at roberta-base were not used when initializing RobertaForTokenClassification: ['lm_head.decoder.weight', 'lm_head.layer_norm.bias', 'lm_head.bias', 'lm_head.dense.weight', 'lm_head.layer_norm.weight', 'lm_head.dense.bias']
- This IS expected if you are initializing RobertaForTokenClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing RobertaForTokenClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of RobertaForTokenClassification were not initialized from the model checkpoint at roberta-base and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able

Epochs 0/3. Running Loss:    0.3673:  24%|█▏   | 49/206 [01:06<03:27,  1.32s/it]INFO:simpletransformers.ner.ner_model: Converting to features started.


  0%|                                                   | 0/300 [00:00<?, ?it/s]

 25%|██████████                               | 74/300 [00:00<00:00, 739.60it/s]

 50%|███████████████████▊                    | 149/300 [00:00<00:00, 744.70it/s]

100%|████████████████████████████████████████| 300/300 [00:00<00:00, 757.44it/s]


Running Evaluation:   0%|                                 | 0/5 [00:00<?, ?it/s]

Running Evaluation:  20%|█████                    | 1/5 [00:00<00:01,  2.37it/s]

Running Evaluation:  40%|██████████               | 2/5 [00:00<00:01,  2.32it/s]

Running Evaluation:  60%|███████████████          | 3/5 [00:01<00:00,  2.29it/s]

Running Evaluation:  80%|████████████████████     | 4/5 [00:01<00:00,  2.30it/s]

Running Evaluation: 100%|█████████████████████████| 5/5 [00:02<00:00,  2.43it/s]
INFO:simpletransformers.ner

Epochs 0/3. Running Loss:    0.2207:  48%|██▍  | 99/206 [02:29<02:22,  1.33s/it]INFO:simpletransformers.ner.ner_model: Converting to features started.


  0%|                                                   | 0/300 [00:00<?, ?it/s]

 25%|██████████▎                              | 75/300 [00:00<00:00, 745.50it/s]

 50%|████████████████████                    | 150/300 [00:00<00:00, 737.39it/s]

100%|████████████████████████████████████████| 300/300 [00:00<00:00, 756.65it/s]


Running Evaluation:   0%|                                 | 0/5 [00:00<?, ?it/s]

Running Evaluation:  20%|█████                    | 1/5 [00:00<00:01,  2.35it/s]

Running Evaluation:  40%|██████████               | 2/5 [00:00<00:01,  2.31it/s]

Running Evaluation:  60%|███████████████          | 3/5 [00:01<00:00,  2.29it/s]

Running Evaluation:  80%|████████████████████     | 4/5 [00:01<00:00,  2.30it/s]

Running Evaluation: 100%|█████████████████████████| 5/5 [00:02<00:00,  2.42it/s]
INFO:simpletransformers.ner

Epochs 0/3. Running Loss:    0.1778:  72%|██▉ | 149/206 [03:51<01:15,  1.33s/it]INFO:simpletransformers.ner.ner_model: Converting to features started.


  0%|                                                   | 0/300 [00:00<?, ?it/s]

 25%|██████████                               | 74/300 [00:00<00:00, 738.65it/s]

 50%|████████████████████                    | 150/300 [00:00<00:00, 738.14it/s]

100%|████████████████████████████████████████| 300/300 [00:00<00:00, 766.45it/s]


Running Evaluation:   0%|                                 | 0/5 [00:00<?, ?it/s]

Running Evaluation:  20%|█████                    | 1/5 [00:00<00:01,  2.38it/s]

Running Evaluation:  40%|██████████               | 2/5 [00:00<00:01,  2.34it/s]

Running Evaluation:  60%|███████████████          | 3/5 [00:01<00:00,  2.28it/s]

Running Evaluation:  80%|████████████████████     | 4/5 [00:01<00:00,  2.29it/s]

Running Evaluation: 100%|█████████████████████████| 5/5 [00:02<00:00,  2.42it/s]
INFO:simpletransformers.ner

Epochs 0/3. Running Loss:    0.2149:  97%|███▊| 199/206 [05:14<00:09,  1.34s/it]INFO:simpletransformers.ner.ner_model: Converting to features started.


  0%|                                                   | 0/300 [00:00<?, ?it/s]

 25%|██████████                               | 74/300 [00:00<00:00, 732.83it/s]

 49%|███████████████████▋                    | 148/300 [00:00<00:00, 734.88it/s]

100%|████████████████████████████████████████| 300/300 [00:00<00:00, 739.04it/s]


Running Evaluation:   0%|                                 | 0/5 [00:00<?, ?it/s]



...

Epochs 2/3. Running Loss:    0.1175:  18%|▉    | 37/206 [00:50<03:44,  1.33s/it]INFO:simpletransformers.ner.ner_model: Converting to features started.


  0%|                                                   | 0/300 [00:00<?, ?it/s]

 25%|██████████                               | 74/300 [00:00<00:00, 739.96it/s]

 49%|███████████████████▋                    | 148/300 [00:00<00:00, 733.24it/s]

100%|████████████████████████████████████████| 300/300 [00:00<00:00, 734.45it/s]


Running Evaluation:   0%|                                 | 0/5 [00:00<?, ?it/s]

Running Evaluation:  20%|█████                    | 1/5 [00:00<00:01,  2.37it/s]

Running Evaluation:  40%|██████████               | 2/5 [00:00<00:01,  2.33it/s]

Running Evaluation:  60%|███████████████          | 3/5 [00:01<00:00,  2.29it/s]

Running Evaluation:  80%|████████████████████     | 4/5 [00:01<00:00,  2.30it/s]

Running Evaluation: 100%|█████████████████████████| 5/5 [00:02<00:00,  2.43it/s]
INFO:simpletransformers.ner

Epochs 2/3. Running Loss:    0.1561:  42%|██   | 87/206 [02:00<02:41,  1.35s/it]INFO:simpletransformers.ner.ner_model: Converting to features started.


  0%|                                                   | 0/300 [00:00<?, ?it/s]

 25%|██████████▎                              | 75/300 [00:00<00:00, 742.09it/s]

 50%|████████████████████                    | 150/300 [00:00<00:00, 700.31it/s]

100%|████████████████████████████████████████| 300/300 [00:00<00:00, 731.20it/s]


Running Evaluation:   0%|                                 | 0/5 [00:00<?, ?it/s]

Running Evaluation:  20%|█████                    | 1/5 [00:00<00:01,  2.36it/s]

Running Evaluation:  40%|██████████               | 2/5 [00:00<00:01,  2.29it/s]

Running Evaluation:  60%|███████████████          | 3/5 [00:01<00:00,  2.27it/s]

Running Evaluation:  80%|████████████████████     | 4/5 [00:01<00:00,  2.28it/s]

Running Evaluation: 100%|█████████████████████████| 5/5 [00:02<00:00,  2.39it/s]
INFO:simpletransformers.ner

Epochs 2/3. Running Loss:    0.1291:  67%|██▋ | 137/206 [03:09<01:32,  1.34s/it]INFO:simpletransformers.ner.ner_model: Converting to features started.


  0%|                                                   | 0/300 [00:00<?, ?it/s]

 24%|█████████▉                               | 73/300 [00:00<00:00, 724.66it/s]

 49%|███████████████████▋                    | 148/300 [00:00<00:00, 737.70it/s]

100%|████████████████████████████████████████| 300/300 [00:00<00:00, 750.83it/s]


Running Evaluation:   0%|                                 | 0/5 [00:00<?, ?it/s]

Running Evaluation:  20%|█████                    | 1/5 [00:00<00:01,  2.35it/s]

Running Evaluation:  40%|██████████               | 2/5 [00:00<00:01,  2.28it/s]

Running Evaluation:  60%|███████████████          | 3/5 [00:01<00:00,  2.26it/s]

Running Evaluation:  80%|████████████████████     | 4/5 [00:01<00:00,  2.27it/s]

Running Evaluation: 100%|█████████████████████████| 5/5 [00:02<00:00,  2.39it/s]
INFO:simpletransformers.ner

Epochs 2/3. Running Loss:    0.1271:  91%|███▋| 187/206 [04:19<00:25,  1.34s/it]INFO:simpletransformers.ner.ner_model: Converting to features started.


  0%|                                                   | 0/300 [00:00<?, ?it/s]

 25%|██████████                               | 74/300 [00:00<00:00, 739.42it/s]

 50%|███████████████████▊                    | 149/300 [00:00<00:00, 743.73it/s]

100%|████████████████████████████████████████| 300/300 [00:00<00:00, 758.49it/s]


Running Evaluation:   0%|                                 | 0/5 [00:00<?, ?it/s]

Running Evaluation:  20%|█████                    | 1/5 [00:00<00:01,  2.36it/s]

Running Evaluation:  40%|██████████               | 2/5 [00:00<00:01,  2.30it/s]

Running Evaluation:  60%|███████████████          | 3/5 [00:01<00:00,  2.26it/s]

Running Evaluation:  80%|████████████████████     | 4/5 [00:01<00:00,  2.27it/s]

Running Evaluation: 100%|█████████████████████████| 5/5 [00:02<00:00,  2.39it/s]
INFO:simpletransformers.ner

Epochs 2/3. Running Loss:    0.1055: 100%|████| 206/206 [04:46<00:00,  1.39s/it]
INFO:simpletransformers.ner.ner_model: Converting to features started.

100%|████████████████████████████████████████| 300/300 [00:00<00:00, 739.14it/s]

Running Evaluation: 100%|█████████████████████████| 5/5 [00:02<00:00,  2.38it/s]
INFO:simpletransformers.ner.ner_model:{'eval_loss': 0.20523332357406615, 'precision': 0.6147110332749562, 'recall': 0.6476014760147601, 'f1_score': 0.6307277628032346}
Epoch 3 of 3: 100%|██████████████████████████████| 3/3 [16:21<00:00, 327.19s/it]
INFO:simpletransformers.ner.ner_model: Training of roberta model complete. Saved to outputs/.

wandb: Waiting for W&B process to finish, PID 1994... (success).
wandb:                                                                                
wandb: Run history:
wandb:   Training loss █▅▄▂▃▂▂▂▂▂▃▂▂▂▂▁▂▂▂▂▂▂▂▁▂▂▂▁▁▁▁▁▁▁▁▁▁▁▁▁
wandb:       eval_loss █▃▂▂▂▂▂▁▁▁▂▂▂▂▂
wandb:        f1_score ▂▁▆▅▆▆▆▆▇▇▇▇▇██
wandb:     global_step ▁▁▁

In [19]:
!python src/evaluation.py {wandb_project} {experiment_suffix} {version_name}  {superclass_tag} {target_tag} {dataset_path}

100%|████████████████████████████████████████████| 1/1 [00:00<00:00, 811.43it/s]


100%|████████████████████████████████████████████| 1/1 [00:00<00:00, 469.53it/s]


Running Prediction: 100%|████████████████████████| 1/1 [00:00<00:00, 110.96it/s]
Skipped snetnece 134.Original sentence:
Through the work of its founder William Irwin Thompson and start - up grants from the Lilly Endowment and the Rockefeller Brothers Fund , the church became a cultural center in which Gary Snyder , Robert Bly , Wendell Berry , Samuel Menash , and Kathleen Raine gave poetry readings , Paul Winter and David Hykes gave concerts , Jerzy Grotowksi and Andre Gregory lectured on theatre , and philosophers such as Gregory Bateson , Francisco Varela , and Thompson himself gave the lectures that became their subsequent books .
Predicted Sentence:
Through the work of its founder William Irwin Thompson and start - up grants from the Lilly Endowment and the Rockefeller Brothers Fund , the church became a cultural center in which Gary Snyder , Robert Bly , Wendell Berry , Samuel Menash , and Kathleen Raine gave poetry readings , Paul Winter and David Hykes gave concerts , Jerzy Gro

Running Prediction: 100%|████████████████████████| 1/1 [00:00<00:00, 102.74it/s]
Skipped snetnece 182.Original sentence:
NY   201 begins at a trumpet interchange with NY   434 ( Vestal Parkway ) in the town of Vestal at the northern edge of Binghamton University .
Predicted Sentence:
NY 201 begins at a trumpet interchange with NY 434 ( Vestal Parkway ) in the town of Vestal at the northern edge of Binghamton University .
100%|████████████████████████████████████████████| 1/1 [00:00<00:00, 634.83it/s]


Running Prediction: 100%|████████████████████████| 1/1 [00:00<00:00, 106.84it/s]
Skipped snetnece 200.Original sentence:
enabled social programming 
 of applications for Facebook , Meebo , OpenSocial , iPhone web applications , and other social platforms , as well as web widgets .
Predicted Sentence:
enabled social programming of applications for Facebook , Meebo , OpenSocial , iPhone web applications , and other social platforms , as well as web widgets .
100%|████████████████████████████████████████████| 1/1 [00:00<00:00, 902.97it/s]


Running Prediction: 100%|████████████████████████| 1/1 [00:00<00:00, 110.92it/s]
Skipped snetnece 262.Original sentence:
The area is the location of a number of cultural institutions , including the Irish Photography Centre ( incorporating the Dublin Institute of Photography , the National Photographic Archive and the Gallery of Photography ) , the Ark Children 's Cultural Centre , the Irish Film Institute , incorporating the Irish Film Archive , the Button Factory , the Arthouse Multimedia Centre , Temple Bar Gallery and Studios , the Project Arts Centre , the Gaiety School of Acting , IBAT College Dublin , the New Theatre , as well as the Irish Stock Exchange .
Predicted Sentence:
The area is the location of a number of cultural institutions , including the Irish Photography Centre ( incorporating the Dublin Institute of Photography , the National Photographic Archive and the Gallery of Photography ) , the Ark Children 's Cultural Centre , the Irish Film Institute , incorporating the

Running Prediction: 100%|████████████████████████| 1/1 [00:00<00:00, 121.41it/s]
confusion matrix:
[[0.279 0.377 0.098 0.098 0.148]
 [0.033 0.742 0.    0.022 0.203]
 [0.008 0.    0.512 0.419 0.062]
 [0.    0.007 0.079 0.776 0.139]
 [0.    0.013 0.001 0.017 0.97 ]]
span recall:
15
61
span recall:
0.2459016393442623
classification report:
              precision    recall  f1-score   support

    B-SCHOOL       0.50      0.28      0.36        61
       B-ORG       0.74      0.74      0.74       454
    I-SCHOOL       0.48      0.51      0.50       129
       I-ORG       0.76      0.78      0.77       763
           O       0.97      0.97      0.97      7077

    accuracy                           0.93      8484
   macro avg       0.69      0.66      0.67      8484
weighted avg       0.93      0.93      0.93      8484

parsed classification report:
{'B-SCH': ['OOL', '0.50', '0.28', '0.36', '61'], 'B-ORG': ['0.74', '0.74', '0.74', '454'], 'I-SCH': ['OOL', '0.48', '0.51', '0.50', '129'], 'I